# DATA PROCESSING

In [3]:
import pandas as pd

def parse_extended_time(tstr):
    """
    Konwertuje czas w formacie 'HH:MM:SS' (nawet gdy HH >= 24)
    na obiekt Timestamp z uwzględnieniem przesunięcia o całe doby.
    """
    h, m, s = tstr.split(':')
    h, m, s = int(h), int(m), int(s)

    day_offset = h // 24
    hour_in_day = h % 24

    base_date = pd.Timestamp(year=2025, month=1, day=1)
    date_time = base_date + pd.Timedelta(days=day_offset, hours=hour_in_day, minutes=m, seconds=s)

    return date_time

# Wczytanie pliku CSV z jawnym określeniem typów
df = pd.read_csv(
    "connection_graph.csv",
    dtype={
        "id": "int64",
        "company": "string",
        "line": "string", 
        "start_stop": "string",
        "end_stop": "string",
        "start_stop_lat": "float64",
        "start_stop_lon": "float64",
        "end_stop_lat": "float64",
        "end_stop_lon": "float64"
    },
    low_memory=False  # To pomaga przy dużych plikach
)

# Konwersja czasów
df["departure_time"] = df["departure_time"].apply(parse_extended_time)
df["arrival_time"] = df["arrival_time"].apply(parse_extended_time)

# Sprawdzenie typów
print(df.dtypes)
print(df.head())

Unnamed: 0                 int64
company           string[python]
line              string[python]
departure_time    datetime64[ns]
arrival_time      datetime64[ns]
start_stop        string[python]
end_stop          string[python]
start_stop_lat           float64
start_stop_lon           float64
end_stop_lat             float64
end_stop_lon             float64
dtype: object
   Unnamed: 0       company line      departure_time        arrival_time  \
0           0  MPK Autobusy    A 2025-01-01 20:52:00 2025-01-01 20:53:00   
1           1  MPK Autobusy    A 2025-01-01 20:53:00 2025-01-01 20:54:00   
2           2  MPK Autobusy    A 2025-01-01 20:54:00 2025-01-01 20:55:00   
3           3  MPK Autobusy    A 2025-01-01 20:55:00 2025-01-01 20:57:00   
4           4  MPK Autobusy    A 2025-01-01 20:57:00 2025-01-01 20:59:00   

             start_stop              end_stop  start_stop_lat  start_stop_lon  \
0   Zajezdnia Obornicka              Paprotna       51.148737       17.021069   
1   

### Creating class Connection and Stop

In [4]:
import re
from datetime import datetime

class Connection:
    def __init__(self, line, start, end, departure_time, arrival_time):
        self.line = line
        self.start: Stop = start 
        self.end: Stop = end  
        self.departure_time = departure_time
        self.arrival_time = arrival_time
        self.travel_time = (arrival_time - departure_time).total_seconds()
        
    def __repr__(self):
        return (f"Connection({self.line}, {self.start.name} -> {self.end.name}, "
                f"{self.departure_time.strftime('%H:%M:%S')} - {self.arrival_time.strftime('%H:%M:%S')})")


class Stop:
    def __init__(self, name, lat, lon):
        self.name = name
        self.lat = lat
        self.lon = lon
        self.connections: Connection = []

    def add_connection(self, connection):
        self.connections.append(connection)

    def __repr__(self):
        return f"Stop({self.name}, {self.lat}, {self.lon})"

    # Function to normalize stop names (e.g. remove dots, spaces)
    @staticmethod
    def normalize_name(name):
        # Removing dots and trimming spaces
        return re.sub(r'\s|\.', '', name).lower()

### Creating graph where each node is a Stop and each edge is a Connection

In [5]:
stop_graph = {}
for _, row in df.iterrows():
    start_name = row["start_stop"]
    end_name = row["end_stop"]
    
    if start_name not in stop_graph:
        stop_graph[start_name] = Stop(start_name, row["start_stop_lat"], row["start_stop_lon"])
    if end_name not in stop_graph:
        stop_graph[end_name] = Stop(end_name, row["end_stop_lat"], row["end_stop_lon"])
    
    connection = Connection(
        line=row["line"],
        start=stop_graph[start_name],
        end=stop_graph[end_name],
        departure_time=row["departure_time"],
        arrival_time=row["arrival_time"]
    )
    
    stop_graph[start_name].add_connection(connection)

# Previewing data
test_stop = next(iter(stop_graph.values()))
print(test_stop)
print(test_stop.connections)




Stop(Zajezdnia Obornicka, 51.14873744, 17.02106859)
[Connection(A, Zajezdnia Obornicka -> Paprotna, 20:52:00 - 20:53:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 21:46:00 - 21:47:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 20:22:00 - 20:23:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 05:36:00 - 05:37:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 05:26:00 - 05:27:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 04:09:00 - 04:10:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 04:39:00 - 04:40:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 05:09:00 - 05:10:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 20:52:00 - 20:53:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 21:46:00 - 21:47:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 20:22:00 - 20:23:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 05:36:00 - 05:37:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 05:26:00 - 05:27:00), Connection(A, Zajezdnia Obornicka -> Paprotna, 04:

In [6]:
import heapq
import time
from datetime import datetime, timedelta

def find_earliest_connection(connections, current_time, previous_line=None, boarding_time=1):

    transfer_delta = timedelta(minutes=boarding_time)
    earliest = None
    for conn in connections:
        # Jeśli nie jeździmy tą samą linią, trzeba doliczyć czas transferu.
        required_departure = current_time if (previous_line is None or conn.line == previous_line) else current_time + transfer_delta
        if conn.departure_time >= required_departure:
            if earliest is None or conn.departure_time < earliest.departure_time:
                earliest = conn
    return earliest



class DijkstraRouter:
    def __init__(self, stop_graph):
        self.stop_graph = stop_graph

    def _validate_stops(self, start_stop, end_stop):
        if start_stop not in self.stop_graph or end_stop not in self.stop_graph:
            print("ERROR: Przystanek startowy lub końcowy nie istnieje w grafie.")
            return False
        return True

    def _initialize_search_structures(self, start_stop, start_time):
        base_date = datetime(2025, 1, 1)
        start_datetime = base_date.replace(hour=start_time.hour, minute=start_time.minute, second=start_time.second)
        
        travel_times = {name: float('inf') for name in self.stop_graph}
        previous = {name: None for name in self.stop_graph}
        arrival_times = {name: None for name in self.stop_graph}
        previous_lines = {name: None for name in self.stop_graph}
        
        travel_times[start_stop] = 0
        arrival_times[start_stop] = start_datetime
        
        return travel_times, previous, arrival_times, previous_lines, start_datetime

    def _group_connections_by_destination(self, current_stop):
        grouped_connections = {}
        for conn in current_stop.connections:
            destination = conn.end.name
            if destination not in grouped_connections:
                grouped_connections[destination] = []
            grouped_connections[destination].append(conn)
        return grouped_connections

    def _reconstruct_route(self, previous, end_stop):
        route = []
        current = end_stop
        while current and previous[current]:
            prev_stop, conn = previous[current]
            route.append(conn)
            current = prev_stop
        route.reverse()
        return route

    def find_route(self, start_stop, end_stop, start_time, boarding_time=1):

        if not self._validate_stops(start_stop, end_stop):
            return None

        start_measure = time.time()

        # Inicjalizacja struktur wyszukiwania
        travel_times, previous, arrival_times, previous_lines, current_time = self._initialize_search_structures(start_stop, start_time)
        
        # Kolejka priorytetowa (open set) dla algorytmu Dijkstry
        open_set = [(0, start_stop)]
        # Zbiór odwiedzonych węzłów (closed set)
        closed_set = set()
        
        while open_set:
            current_travel_time, current_stop_name = heapq.heappop(open_set)
            
            # Jeśli przystanek już był przetwarzany, pomijamy go
            if current_stop_name in closed_set:
                continue
            
            # Dodajemy przystanek do zbioru zamkniętych
            closed_set.add(current_stop_name)
            
            # Jeśli dotarliśmy do celu, przerywamy pętlę
            if current_stop_name == end_stop:
                break
            
            current_stop = self.stop_graph[current_stop_name]
            current_arrival_time = arrival_times[current_stop_name]
            current_line = previous_lines[current_stop_name]
            
            # Grupowanie połączeń wg przystanków docelowych
            grouped_connections = self._group_connections_by_destination(current_stop)
            
            for next_stop_name, conns in grouped_connections.items():
                # Znajdź najwcześniejsze połączenie z uwzględnieniem zasad przesiadek
                earliest_conn = find_earliest_connection(
                    conns, current_arrival_time, 
                    previous_line=current_line, 
                    boarding_time=boarding_time
                )
                
                if earliest_conn is None:
                    continue
                
                travel_time = (earliest_conn.arrival_time - current_arrival_time).total_seconds() / 60
                
                # Aktualizujemy tylko, jeśli znaleziono szybszą trasę
                if current_travel_time + travel_time < travel_times[next_stop_name]:
                    travel_times[next_stop_name] = current_travel_time + travel_time
                    previous[next_stop_name] = (current_stop_name, earliest_conn)
                    arrival_times[next_stop_name] = earliest_conn.arrival_time
                    previous_lines[next_stop_name] = earliest_conn.line
                    
                    heapq.heappush(open_set, (travel_times[next_stop_name], next_stop_name))
        
        end_measure = time.time()
          
        if travel_times[end_stop] == float('inf'):
            print("DEBUG: Brak dostępnej trasy!")
            return None
        
        # Rekonstrukcja trasy
        route = self._reconstruct_route(previous, end_stop)

        transfer_count = 0
        for i in range(1, len(route)):
            if route[i].line != route[i-1].line:
                transfer_count += 1
        
        # Obliczenie całkowitego czasu podróży
        hours = travel_times[end_stop] // 60
        minutes = travel_times[end_stop] % 60
        total_cost = f"{int(hours)}h {int(minutes)}min"
        
        return {
            'route': route,
            'total_cost': total_cost,
            'calculation_time': end_measure - start_measure,
            'transfers': transfer_count
        }




# --- Użycie routera ---
router = DijkstraRouter(stop_graph)

start_stop = "PL. JANA PAWŁA II"
end_stop = "PL. GRUNWALDZKI"
start_time_str = "07:00:00"
start_time = datetime.strptime(start_time_str, "%H:%M:%S")

result = router.find_route(start_stop, end_stop, start_time)

if result:
    print("\nHarmonogram przejazdu:")
    for connection in result['route']:
        print(f"Linia: {connection.line}, "
              f"Z: {connection.start.name} o {connection.departure_time.strftime('%H:%M:%S')}, "
              f"Do: {connection.end.name} o {connection.arrival_time.strftime('%H:%M:%S')}")
    print(f"Liczba przesiadek: {result['transfers']}")
    print(f"\nKoszt trasy (min): {result['total_cost']}")
    print(f"Czas obliczeń: {result['calculation_time']:.4f} sekund")
else:
    print("Nie znaleziono trasy.")



Harmonogram przejazdu:
Linia: 142, Z: PL. JANA PAWŁA II o 07:01:00, Do: Rynek o 07:04:00
Linia: 10, Z: Rynek o 07:05:00, Do: Zamkowa o 07:06:00
Linia: 10, Z: Zamkowa o 07:06:00, Do: Świdnicka o 07:08:00
Linia: 10, Z: Świdnicka o 07:08:00, Do: GALERIA DOMINIKAŃSKA o 07:10:00
Linia: 12, Z: GALERIA DOMINIKAŃSKA o 07:11:00, Do: Urząd Wojewódzki (Impart) o 07:14:00
Linia: 12, Z: Urząd Wojewódzki (Impart) o 07:14:00, Do: most Grunwaldzki o 07:16:00
Linia: 12, Z: most Grunwaldzki o 07:16:00, Do: PL. GRUNWALDZKI o 07:18:00
Liczba przesiadek: 2

Koszt trasy (min): 0h 18min
Czas obliczeń: 0.7079 sekund


In [ ]:
class AStarRouter:
    def __init__(self, stop_graph, heuristic_function):
        self.stop_graph = stop_graph
        self.heuristic = heuristic_function

    def _validate_stops(self, start_stop, end_stop):
        if start_stop not in self.stop_graph or end_stop not in self.stop_graph:
            print("ERROR: Przystanek startowy lub końcowy nie istnieje w grafie.")
            return False
        return True

    def _initialize_search_structures(self, start_stop, start_time):
        base_date = datetime(2025, 1, 1)
        start_datetime = base_date.replace(hour=start_time.hour, minute=start_time.minute, second=start_time.second)
        
        travel_times = {name: float('inf') for name in self.stop_graph}
        previous = {name: None for name in self.stop_graph}
        arrival_times = {name: None for name in self.stop_graph}
        previous_lines = {name: None for name in self.stop_graph}
        
        travel_times[start_stop] = 0
        arrival_times[start_stop] = start_datetime
        
        return travel_times, previous, arrival_times, previous_lines, start_datetime

    def _group_connections_by_destination(self, current_stop):
        grouped_connections = {}
        for conn in current_stop.connections:
            destination = conn.end.name
            if destination not in grouped_connections:
                grouped_connections[destination] = []
            grouped_connections[destination].append(conn)
        return grouped_connections

    def _reconstruct_route(self, previous, end_stop):
        route = []
        current = end_stop
        while current and previous[current]:
            prev_stop, conn = previous[current]
            route.append(conn)
            current = prev_stop
        route.reverse()
        return route

    def find_route(self, start_stop, end_stop, start_time, boarding_time=1):
        if not self._validate_stops(start_stop, end_stop):
            return None

        start_measure = time.time()
        
        travel_times, previous, arrival_times, previous_lines, current_time = self._initialize_search_structures(start_stop, start_time)
        
        open_set = [(0, 0, start_stop)]
        closed_set = set()
        
        while open_set:
            current_f, current_g, current_stop_name = heapq.heappop(open_set)
            
            if current_stop_name in closed_set:
                continue
            
            closed_set.add(current_stop_name)
            
            if current_stop_name == end_stop:
                break
            
            current_stop = self.stop_graph[current_stop_name]
            current_arrival_time = arrival_times[current_stop_name]
            current_line = previous_lines[current_stop_name]
            
            grouped_connections = self._group_connections_by_destination(current_stop)
            
            for next_stop_name, conns in grouped_connections.items():
                if next_stop_name in closed_set:
                    continue
                
                earliest_conn = find_earliest_connection(conns, current_arrival_time, previous_line=current_line, boarding_time=boarding_time)
                
                if earliest_conn is None:
                    continue
                
                travel_time = (earliest_conn.arrival_time - current_arrival_time).total_seconds() / 60

                heuristic_args = {
                    'current_line': current_line,
                    'next_line': earliest_conn.line,
                    'current_stop': current_stop,
                    'end_stop': self.stop_graph[end_stop],
                    'current_time': current_arrival_time,
                    'start_time': start_time
                }
                heuristic = self.heuristic(**heuristic_args)
                
                new_g = current_g + travel_time
                h_cost = heuristic
                f_cost = new_g + h_cost
                
                if new_g < travel_times[next_stop_name]:
                    travel_times[next_stop_name] = new_g
                    previous[next_stop_name] = (current_stop_name, earliest_conn)
                    arrival_times[next_stop_name] = earliest_conn.arrival_time
                    previous_lines[next_stop_name] = earliest_conn.line
                    
                    heapq.heappush(open_set, (f_cost, new_g, next_stop_name))
        
        end_measure = time.time()
        
        if travel_times[end_stop] == float('inf'):
            print("DEBUG: Brak dostępnej trasy!")
            return None
        
        route = self._reconstruct_route(previous, end_stop)

        transfer_count = 0
        for i in range(1, len(route)):
            if route[i].line != route[i-1].line:
                transfer_count += 1
        
        hours = travel_times[end_stop] // 60
        minutes = travel_times[end_stop] % 60
        total_cost = f"{int(hours)}h {int(minutes)}min"
        
        return {
            'route': route,
            'total_cost': total_cost,
            'calculation_time': end_measure - start_measure,
            'transfers': transfer_count
        }



# Funkcja odpowiedzialna za obliczanie kary za przesiadki
def transfer_penalty_function(transfer_penalty = 150, **kwargs):
    current_line = kwargs['current_line']
    next_line = kwargs['next_line']

    if current_line and current_line != next_line:
        return transfer_penalty
    return 0

def haversine_distance(lat1, lon1, lat2, lon2):
    from math import radians, sin, cos, sqrt, atan2

    R = 6371.0  # Średnia promień Ziemi w km

    lat1 = radians(lat1)
    lon1 = radians(lon1)
    lat2 = radians(lat2)
    lon2 = radians(lon2)

    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))

    distance = R * c
    return distance


def distance_penalty_function(distance_penalty = 100, **kwargs):
    current_stop = kwargs['current_stop']
    end_stop = kwargs['end_stop']
    return distance_penalty * haversine_distance(current_stop.lat, current_stop.lon, end_stop.lat, end_stop.lon)

def time_penalty_function(time_penalty =100, **kwargs):
    current_time = kwargs['current_time']
    start_time = kwargs['start_time']
    return time_penalty * ((current_time - start_time).total_seconds() / 60)

def zero_heuristic(**kwargs):
    return 0

router = AStarRouter(stop_graph, distance_penalty_function)


start_stop = "PL. JANA PAWŁA II"
end_stop = "PL. GRUNWALDZKI"
start_time_str = "07:00:00"
start_time = datetime.strptime(start_time_str, "%H:%M:%S")

#Find stop im

result = router.find_route(start_stop, end_stop, start_time)

if result:
    print("\nHarmonogram przejazdu:")
    for connection in result['route']:
        print(f"Linia: {connection.line}, "
              f"Z: {connection.start.name} o {connection.departure_time.strftime('%H:%M:%S')}, "
              f"Do: {connection.end.name} o {connection.arrival_time.strftime('%H:%M:%S')}")
    print(f"Liczba przesiadek: {result['transfers']}")
    print(f"\nKoszt trasy (min): {result['total_cost']}")
    print(f"Czas obliczeń: {result['calculation_time']:.4f} sekund")
else:
    print("Nie znaleziono trasy.")


Harmonogram przejazdu:
Linia: 142, Z: PL. JANA PAWŁA II o 07:01:00, Do: Rynek o 07:04:00
Linia: 10, Z: Rynek o 07:05:00, Do: Zamkowa o 07:06:00
Linia: 10, Z: Zamkowa o 07:06:00, Do: Świdnicka o 07:08:00
Linia: 10, Z: Świdnicka o 07:08:00, Do: GALERIA DOMINIKAŃSKA o 07:10:00
Linia: 12, Z: GALERIA DOMINIKAŃSKA o 07:11:00, Do: Urząd Wojewódzki (Impart) o 07:14:00
Linia: 12, Z: Urząd Wojewódzki (Impart) o 07:14:00, Do: most Grunwaldzki o 07:16:00
Linia: 12, Z: most Grunwaldzki o 07:16:00, Do: PL. GRUNWALDZKI o 07:18:00
Liczba przesiadek: 2

Koszt trasy (min): 0h 18min
Czas obliczeń: 0.4191 sekund


In [36]:
import math


def time_based_heuristic(start_stop, end_stop):
    """
    Heuristic based on estimated travel time between stops.
    Uses Haversine formula to calculate distance and estimates time.
    
    :param start_stop: Starting Stop object
    :param end_stop: Destination Stop object
    :return: Estimated travel time in minutes
    """
    # Haversine formula to calculate distance between two points on Earth
    R = 6371  # Earth's radius in kilometers
    
    # Convert latitude and longitude to radians
    lat1, lon1 = math.radians(start_stop.lat), math.radians(start_stop.lon)
    lat2, lon2 = math.radians(end_stop.lat), math.radians(end_stop.lon)
    
    # Differences
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    
    # Haversine formula
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    distance = R * c
    
    # Estimate travel time (assume average speed of 50 km/h)
    estimated_time = (distance / 50) * 60  # convert to minutes
    
    return estimated_time

def transfer_based_heuristic(start_stop, end_stop):
    """
    Heuristic optimized for minimizing transfers.
    Ignores start and end stops for transfer calculation.
    
    :param start_stop: Starting Stop object
    :param end_stop: Destination Stop object
    :return: Estimated transfer penalty
    """
    # Haversine formula to calculate straight-line distance
    R = 6371  # Earth's radius in kilometers
    
    # Convert latitude and longitude to radians
    lat1, lon1 = math.radians(start_stop.lat), math.radians(start_stop.lon)
    lat2, lon2 = math.radians(end_stop.lat), math.radians(end_stop.lon)
    
    # Differences
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    
    # Haversine formula
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    distance = R * c
    
    # Aggressive penalty for transfers
    # This will make the algorithm strongly prefer routes with fewer transfers
    penalty = 10000000  # High base penalty for transfers
    
    # Estimate potential transfers: assume 1 transfer per significant distance
    estimated_transfers = max(0, math.ceil(distance / 10))  # lower threshold for transfers
    
    # Return a penalty that strongly discourages transfers
    return estimated_transfers * penalty


def transfer_based_heuristic2(start_stop, end_stop):
    """
    Heuristic optimized for minimizing transfers.
    
    :param start_stop: Starting Stop object
    :param end_stop: Destination Stop object
    :return: Estimated transfer penalty
    """
    # Jeśli start_stop różni się od end_stop, dodaj karę za przesiadkę
    transfer_penalty = 1000000 if start_stop.name != end_stop.name else 0
    
    return transfer_penalty

def zero_heuristic(start_stop, end_stop, transfers=0):
    return 0



# --- Użycie routera A* ---
router = AStarRouter(stop_graph)


start_stop = "Wilczyce - Sosnowa"
end_stop = "Kołobrzeska"
start_time_str = "07:00:00"
start_time = datetime.strptime(start_time_str, "%H:%M:%S")

#Find stop im

result = router.find_route(start_stop, end_stop, start_time)

if result:
    print("\nHarmonogram przejazdu:")
    for connection in result['route']:
        print(f"Linia: {connection.line}, "
              f"Z: {connection.start.name} o {connection.departure_time.strftime('%H:%M:%S')}, "
              f"Do: {connection.end.name} o {connection.arrival_time.strftime('%H:%M:%S')}")
    print(f"Liczba przesiadek: {result['transfers']}")
    print(f"\nKoszt trasy (min): {result['total_cost']}")
    print(f"Czas obliczeń: {result['calculation_time']:.4f} sekund")
else:
    print("Nie znaleziono trasy.")


ValueError: not enough values to unpack (expected 4, got 3)

# ZMIENIC FIND EARLIEST CONNECTION W A STAR 

In [9]:
def get_routes_for_line(line, stop_graph):
    routes = []
    for stop in stop_graph.values():
        for connection in stop.connections:
            if connection.line == line:
                routes.append(connection)
    
    # Sort the routes by departure_time
    routes.sort(key=lambda conn: conn.departure_time)
    
    return routes


line = "911"  # Example line number
routes = get_routes_for_line(line, stop_graph)

# Displaying the results
for route in routes:
    print(route)



Connection(911, Kiełczów - pętla (Plac Jana Gdaka) -> Kiełczów - WODROL, 03:36:00 - 03:37:00)
Connection(911, Kiełczów - pętla (Plac Jana Gdaka) -> Kiełczów - WODROL, 03:36:00 - 03:37:00)
Connection(911, Kiełczów - WODROL -> Kiełczów - osiedle, 03:37:00 - 03:38:00)
Connection(911, Kiełczów - WODROL -> Kiełczów - osiedle, 03:37:00 - 03:38:00)
Connection(911, Kiełczów - osiedle -> Wilczyce - Sosnowa, 03:38:00 - 03:39:00)
Connection(911, Kiełczów - osiedle -> Wilczyce - Sosnowa, 03:38:00 - 03:39:00)
Connection(911, Wilczyce - Sosnowa -> Wilczyce - Dębowa, 03:39:00 - 03:40:00)
Connection(911, Wilczyce - Sosnowa -> Wilczyce - Dębowa, 03:39:00 - 03:40:00)
Connection(911, Wilczyce - Dębowa -> Wilczyce - Dworska, 03:40:00 - 03:41:00)
Connection(911, Wilczyce - Dębowa -> Wilczyce - Dworska, 03:40:00 - 03:41:00)
Connection(911, Wilczyce - Dworska -> Wilczyce - Borowa, 03:41:00 - 03:42:00)
Connection(911, Wilczyce - Dworska -> Wilczyce - Borowa, 03:41:00 - 03:42:00)
Connection(911, Wilczyce - Bor

In [5]:
import networkx as nx
import matplotlib.pyplot as plt

# Funkcja do filtrowania połączeń dla danej linii
def filter_connections_for_line(stop_graph, line):
    filtered_graph = {}
    for stop, stop_obj in stop_graph.items():
        # Filtrowanie przystanków, które mają połączenia z wybraną linią
        has_connection = any(connection.line == line for connection in stop_obj.connections)
        if has_connection:
            filtered_graph[stop] = stop_obj
    return filtered_graph

# Funkcja do rysowania grafu
def draw_graph(stop_graph, line=None):
    G = nx.DiGraph()

    # Filtruj dane, jeśli podano linię
    if line:
        stop_graph = filter_connections_for_line(stop_graph, line)

    # Dodaj węzły do grafu
    for stop, stop_obj in stop_graph.items():
        G.add_node(stop, label=stop_obj.name, pos=(stop_obj.lon, stop_obj.lat))

    # Dodaj krawędzie (połączenia) do grafu
    for stop, stop_obj in stop_graph.items():
        for connection in stop_obj.connections:
            if line and connection.line == line:
                G.add_edge(connection.start.name, connection.end.name, label=connection.line)

    # Pobieramy pozycje węzłów
    pos = nx.get_node_attributes(G, 'pos')

    if line:
        plt.figure(figsize=(40, 40))
    else:
        plt.figure(figsize=(150, 150))
        
    nx.draw(G, pos, with_labels=True, node_size=1000, node_color="lightblue", edge_color="gray", font_size=10, font_weight="bold", arrows=True)

    # Etykiety krawędzi (linii)
    edge_labels = nx.get_edge_attributes(G, 'label')
    nx.draw_networkx_edge_labels(G, pos, edge_labels=edge_labels, font_size=8)

    plt.title(f"Graf przystanków i połączeń dla linii {line}" if line else "Graf wszystkich przystanków i połączeń")
    plt.show()

# Wywołanie funkcji:
draw_graph(stop_graph)


In [14]:
import heapq
import time
from datetime import datetime, timedelta
import math

def haversine_distance(lat1, lon1, lat2, lon2):
    """
    Obliczenie odległości między punktami geograficznymi za pomocą formuły Haversine'a.
    """
    lat1, lon1, lat2, lon2 = map(math.radians, [lat1, lon1, lat2, lon2])
    
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2
    c = 2 * math.asin(math.sqrt(a))
    
    r = 6371
    return c * r

class AStarRouter2:
    def __init__(self, stop_graph):
        self.stop_graph = stop_graph

    def heuristic(self, current_stop, end_stop):
        """
        Estymacja kosztu (odległości) między przystankami.
        """
        current = self.stop_graph[current_stop]
        end = self.stop_graph[end_stop]
        return haversine_distance(current.lat, current.lon, end.lat, end.lon)

    def find_route(self, start_stop, end_stop, start_time, mode='least_transfers', 
                   boarding_time=1, max_transfer_penalty=120, max_transfer_count=100):
        """
        Szukanie trasy z zaawansowaną minimalizacją przesiadek.
        """
        base_date = datetime(2025, 1, 1)
        start_datetime = base_date.replace(hour=start_time.hour, minute=start_time.minute, second=start_time.second)
        
        if start_stop not in self.stop_graph or end_stop not in self.stop_graph:
            print("ERROR: Przystanek początkowy lub końcowy nie istnieje.")
            return None

        # Inicjalizacja struktur danych
        travel_times = {name: float('inf') for name in self.stop_graph}
        travel_times[start_stop] = 0
        
        arrival_times = {name: None for name in self.stop_graph}
        arrival_times[start_stop] = start_datetime
        
        previous = {name: None for name in self.stop_graph}
        previous_lines = {name: None for name in self.stop_graph}
        transfers = {name: 0 for name in self.stop_graph}
        
        # Priorytetowa kolejka dla A*
        open_set = [(
            self.heuristic(start_stop, end_stop), 
            0,  # koszt podróży 
            0,  # liczba przesiadek
            start_stop
        )]
        
        closed_set = set()
        start_calculation = time.time()
        
        while open_set:
            current_f, current_g, current_transfers, current_stop_name = heapq.heappop(open_set)
            
            if current_stop_name == end_stop:
                break
            
            if current_stop_name in closed_set:
                continue
            
            # Ogranicz maksymalną liczbę przesiadek
            if current_transfers > max_transfer_count:
                continue
            
            closed_set.add(current_stop_name)
            
            current_stop = self.stop_graph[current_stop_name]
            current_time = arrival_times[current_stop_name]
            current_line = previous_lines[current_stop_name]
            
            # Grupowanie połączeń wg destynacji
            connections_by_dest = {}
            for conn in current_stop.connections:
                destination = conn.end.name
                if destination not in connections_by_dest:
                    connections_by_dest[destination] = []
                connections_by_dest[destination].append(conn)
            
            for next_stop_name, conns in connections_by_dest.items():
                if next_stop_name in closed_set:
                    continue
                
                # Znajdź najwcześniejsze połączenie
                earliest_conn = find_earliest_connection(
                    conns, current_time, 
                    previous_line=current_line, 
                    boarding_time=boarding_time
                )
                
                if earliest_conn is None:
                    continue
                
                # Wylicz koszt podróży
                travel_time = (earliest_conn.arrival_time - current_time).total_seconds() / 60
                
                # Dynamiczna kara za przesiadki
                transfer_penalty = 0
                new_transfers = current_transfers
                if current_line and current_line != earliest_conn.line:
                    transfer_penalty = max_transfer_penalty
                    new_transfers += 1
                
                new_g = current_g + travel_time + transfer_penalty
                
                # Bardziej złożona heurystyka
                if mode == 'least_transfers':
                    h_cost = (
                        self.heuristic(next_stop_name, end_stop) / 5 + 
                        (new_transfers * max_transfer_penalty * 2)
                    )
                else:
                    h_cost = self.heuristic(next_stop_name, end_stop)
                
                f_cost = new_g + h_cost
                
                # Sprawdź, czy nowa ścieżka jest lepsza
                if new_g < travel_times[next_stop_name]:
                    travel_times[next_stop_name] = new_g
                    previous[next_stop_name] = (current_stop_name, earliest_conn)
                    arrival_times[next_stop_name] = earliest_conn.arrival_time
                    previous_lines[next_stop_name] = earliest_conn.line
                    transfers[next_stop_name] = new_transfers
                    
                    heapq.heappush(open_set, (f_cost, new_g, new_transfers, next_stop_name))
        
        end_calculation = time.time()
        
        if travel_times[end_stop] == float('inf'):
            print("DEBUG: Brak dostępnej trasy!")
            return None
        
        # Rekonstrukcja trasy
        route = []
        current = end_stop
        while current and previous[current]:
            prev_stop, conn = previous[current]
            route.append(conn)
            current = prev_stop
        route.reverse()
        
        # Dokładne obliczenie całkowitego czasu podróży
        first_departure = route[0].departure_time
        last_arrival = route[-1].arrival_time
        total_travel_time = (last_arrival - first_departure).total_seconds() / 60
        
        # Konwersja czasu podróży
        travel_hours = int(total_travel_time // 60)
        travel_minutes = int(total_travel_time % 60)
        travel_time_str = f"{travel_hours}h {travel_minutes}min"
        
        # Obliczenie kosztu trasy w minutach
        route_cost_minutes = int(travel_times[end_stop])
        
        return {
            'route': route,
            'total_cost_minutes': route_cost_minutes,
            'total_travel_time': travel_time_str,
            'calculation_time': end_calculation - start_calculation,
            'transfers': transfers[end_stop],
            'first_departure': first_departure,
            'last_arrival': last_arrival
        }

# Pozostała część kodu bez zmian

router = AStarRouter2(stop_graph)


start_stop = "Wilczyce - Sosnowa"
end_stop = "Kołobrzeska"
start_time_str = "07:00:00"
start_time = datetime.strptime(start_time_str, "%H:%M:%S")

#Find stop im

result = router.find_route(start_stop, end_stop, start_time)

if result:
    print("\nHarmonogram przejazdu:")
    for connection in result['route']:
        print(f"Linia: {connection.line}, "
              f"Z: {connection.start.name} o {connection.departure_time.strftime('%H:%M:%S')}, "
              f"Do: {connection.end.name} o {connection.arrival_time.strftime('%H:%M:%S')}")
    print(f"Liczba przesiadek: {result['transfers']}")
    #print(f"\nKoszt trasy (min): {result['total_cost']}")
    print(f"Czas obliczeń: {result['calculation_time']:.4f} sekund")
else:
    print("Nie znaleziono trasy.")



Harmonogram przejazdu:
Linia: 911, Z: Wilczyce - Sosnowa o 07:10:00, Do: Wilczyce - Dębowa o 07:11:00
Linia: 911, Z: Wilczyce - Dębowa o 07:11:00, Do: Wilczyce - Dworska o 07:12:00
Linia: 911, Z: Wilczyce - Dworska o 07:12:00, Do: Wilczyce - Borowa o 07:13:00
Linia: 911, Z: Wilczyce - Borowa o 07:13:00, Do: Wilczyce - Wrocławska (na wys. nr 1F) o 07:14:00
Linia: 911, Z: Wilczyce - Wrocławska (na wys. nr 1F) o 07:14:00, Do: Wilczyce o 07:14:00
Linia: 911, Z: Wilczyce o 07:14:00, Do: Mroźna o 07:15:00
Linia: 911, Z: Mroźna o 07:15:00, Do: Kurlandzka o 07:15:00
Linia: 911, Z: Kurlandzka o 07:15:00, Do: Zgorzelisko o 07:16:00
Linia: 911, Z: Zgorzelisko o 07:16:00, Do: Palacha o 07:17:00
Linia: 911, Z: Palacha o 07:17:00, Do: Szewczenki o 07:18:00
Linia: 911, Z: Szewczenki o 07:18:00, Do: Gorlicka o 07:19:00
Linia: 911, Z: Gorlicka o 07:19:00, Do: MULICKA o 07:20:00
Linia: 911, Z: MULICKA o 07:20:00, Do: Psie Pole (Rondo Lotników Polskich) o 07:21:00
Linia: 911, Z: Psie Pole (Rondo Lotnikó

In [12]:
import heapq
import time
from datetime import datetime, timedelta
from itertools import permutations
import sys

class TSPSolver:
    def __init__(self, stop_graph, optimization_criterion='t'):
        self.stop_graph = stop_graph
        self.optimization_criterion = optimization_criterion
        self.router = DijkstraRouter(stop_graph)
        self.memo = {}

    def solve(self, start_stop, stops_to_visit, start_time):
        start_measure = time.time()
        
        # Add start stop to the list if not already present (for return)
        all_stops = [start_stop] + [s for s in stops_to_visit if s != start_stop]
        
        # Precompute all pairwise routes
        self._precompute_routes(all_stops, start_time)
        
        # Initialize best route variables
        best_route_segments = None
        best_cost = float('inf')
        best_order = None
        total_time_minutes = 0
        
        # Try all permutations of intermediate stops (brute-force for small n)
        for perm in permutations(stops_to_visit):
            current_route = [start_stop] + list(perm) + [start_stop]
            total_cost = 0
            route_segments = []
            current_start_time = start_time
            
            valid = True
            for i in range(len(current_route)-1):
                from_stop = current_route[i]
                to_stop = current_route[i+1]
                
                # Compute route with current start time
                segment = self._recompute_route_with_time(from_stop, to_stop, current_start_time)
                if segment is None:
                    valid = False
                    break
                    
                if self.optimization_criterion == 't':
                    segment_cost = segment['travel_time_minutes']
                else:  # 'p'
                    segment_cost = segment['transfers']
                
                total_cost += segment_cost
                route_segments.append(segment)
                current_start_time = segment['route'][-1].arrival_time
            
            if valid and total_cost < best_cost:
                best_cost = total_cost
                best_route_segments = route_segments
                best_order = current_route
                if best_route_segments:
                    start = best_route_segments[0]['route'][0].departure_time
                    end = best_route_segments[-1]['route'][-1].arrival_time
                    total_time_minutes = (end - start).total_seconds() / 60
        
        if best_route_segments is not None:
            # Reconstruct the full route from segments
            full_route = []
            for segment in best_route_segments:
                full_route.extend(segment['route'])
            
            end_measure = time.time()
            
            return {
                'route': full_route,
                'total_cost': best_cost,
                'calculation_time': end_measure - start_measure,
                'transfers': sum(seg['transfers'] for seg in best_route_segments),
                'total_time_minutes': total_time_minutes,
                'stop_order': best_order
            }
        else:
            end_measure = time.time()
            return None
    
    def _precompute_routes(self, stops, start_time):
        # Clear previous memoization
        self.memo = {}
        
        # Compute routes between all pairs of stops
        for i in range(len(stops)):
            for j in range(len(stops)):
                if i == j:
                    continue
                
                from_stop = stops[i]
                to_stop = stops[j]
                
                if (from_stop, to_stop) in self.memo:
                    continue
                
                # For the first segment, use the given start time
                if i == 0:
                    segment_start_time = start_time
                else:
                    # For subsequent segments, we don't know the exact time yet
                    segment_start_time = None
                
                # Store None for now, we'll compute exact times during reconstruction
                self.memo[(from_stop, to_stop)] = None
    
    def _recompute_route_with_time(self, from_stop, to_stop, start_time):
        # Compute route with exact start time
        result = self.router.find_route(from_stop, to_stop, start_time)
        if result:
            travel_time_minutes = sum(conn.travel_time for conn in result['route']) / 60
            result['travel_time_minutes'] = travel_time_minutes
        return result

def main():
    # Read input
    start_stop = "Wilczyce - Sosnowa"
    stops_to_visit = ["Kołobrzeska", "PL. JANA PAWŁA II", "PL. GRUNWALDZKI"]
    optimization_criterion = 'p'  # 't' for time, 'p' for transfers
    start_time_str = "07:00:00"
    
    # Parse start time
    try:
        h, m, s = map(int, start_time_str.split(':'))
        base_date = datetime(2025, 1, 1)
        start_time = base_date.replace(hour=h, minute=m, second=s)
    except:
        print("Invalid time format. Use HH:MM:SS")
        return
    
    # Validate stops
    for stop in [start_stop] + stops_to_visit:
        if stop not in stop_graph:
            print(f"ERROR: Stop '{stop}' not found in the graph.", file=sys.stderr)
            return
    
    # Solve the problem
    solver = TSPSolver(stop_graph, optimization_criterion)
    solution = solver.solve(start_stop, stops_to_visit, start_time)
    
    if not solution:
        print("No route found that visits all stops.", file=sys.stderr)
        return
    
    # Print the schedule to stdout
    print("\nHarmonogram przejazdu:")
    current_line = None
    current_start_stop = None
    current_departure_time = None
    
    for i, conn in enumerate(solution['route']):
        if conn.line != current_line:
            # Print previous line if exists
            if current_line is not None:
                print(f"{current_line}, {current_start_stop} o {current_departure_time.strftime('%H:%M:%S')}, "
                      f"{prev_conn.end.name} o {prev_conn.arrival_time.strftime('%H:%M:%S')}")
            
            # Start new line
            current_line = conn.line
            current_start_stop = conn.start.name
            current_departure_time = conn.departure_time
        
        prev_conn = conn
    
    # Print the last line
    if current_line is not None:
        print(f"{current_line}, {current_start_stop} o {current_departure_time.strftime('%H:%M:%S')}, "
              f"{prev_conn.end.name} o {prev_conn.arrival_time.strftime('%H:%M:%S')}")
    
    # Print cost and calculation time to stderr
    if optimization_criterion == 't':
        cost_str = f"Total travel time: {solution['total_time_minutes']:.1f} minutes"
    else:
        cost_str = f"Total transfers: {solution['transfers']}"
    
    print(f"{cost_str}\nCalculation time: {solution['calculation_time']:.4f} seconds", file=sys.stderr)

if __name__ == "__main__":
    main()


Harmonogram przejazdu:
911, Wilczyce - Sosnowa o 07:10:00, C.H. Korona o 07:25:00
131, C.H. Korona o 07:26:00, PL. GRUNWALDZKI o 07:37:00
D, PL. GRUNWALDZKI o 07:37:00, Renoma o 07:48:00
148, Renoma o 07:51:00, Kołobrzeska o 08:13:00
142, Kołobrzeska o 08:16:00, PL. JANA PAWŁA II o 08:37:00
15, PL. JANA PAWŁA II o 08:37:00, Broniewskiego o 08:53:00
D, Broniewskiego o 08:54:00, Psie Pole (Rondo Lotników Polskich) o 09:09:00
131, Psie Pole (Rondo Lotników Polskich) o 09:13:00, Żmudzka o 09:18:00
121, Żmudzka o 09:19:00, Kiełczowska (Cmentarz) o 09:20:00
931, Kiełczowska (Cmentarz) o 09:24:00, Kiełczów - WODROL o 09:30:00
911, Kiełczów - WODROL o 09:36:00, Wilczyce - Sosnowa o 09:38:00


Total transfers: 7
Calculation time: 26.7268 seconds
